Parsing semantyczny z wykorzystaniem technik uczenia maszynowego
================================================================

Wprowadzenie
------------
Problem wykrywania slotów i ich wartości w wypowiedziach użytkownika można sformułować jako zadanie
polegające na przewidywaniu dla poszczególnych słów etykiet wskazujących na to czy i do jakiego
slotu dane słowo należy.

> chciałbym zarezerwować stolik na jutro**/day** na godzinę dwunastą**/hour** czterdzieści**/hour** pięć**/hour** na pięć**/size** osób

Granice slotów oznacza się korzystając z wybranego schematu etykietowania.

### Schemat IOB

| Prefix | Znaczenie                  |
|:------:|:---------------------------|
| I      | wnętrze slotu (inside)     |
| O      | poza slotem (outside)      |
| B      | początek slotu (beginning) |

> chciałbym zarezerwować stolik na jutro**/B-day** na godzinę dwunastą**/B-hour** czterdzieści**/I-hour** pięć**/I-hour** na pięć**/B-size** osób

### Schemat IOBES

| Prefix | Znaczenie                  |
|:------:|:---------------------------|
| I      | wnętrze slotu (inside)     |
| O      | poza slotem (outside)      |
| B      | początek slotu (beginning) |
| E      | koniec slotu (ending)      |
| S      | pojedyncze słowo (single)  |

> chciałbym zarezerwować stolik na jutro**/S-day** na godzinę dwunastą**/B-hour** czterdzieści**/I-hour** pięć**/E-hour** na pięć**/S-size** osób

Jeżeli dla tak sformułowanego zadania przygotujemy zbiór danych
złożony z wypowiedzi użytkownika z oznaczonymi slotami (tzw. *zbiór uczący*),
to możemy zastosować techniki (nadzorowanego) uczenia maszynowego w celu zbudowania modelu
annotującego wypowiedzi użytkownika etykietami slotów.

Do zbudowania takiego modelu można wykorzystać między innymi:

 1. warunkowe pola losowe (Lafferty i in.; 2001),

 2. rekurencyjne sieci neuronowe, np. sieci LSTM (Hochreiter i Schmidhuber; 1997),

 3. transformery (Vaswani i in., 2017).

Przykład
--------
Skorzystamy ze zbioru danych przygotowanego przez Schustera (2019).

In [1]:
!mkdir -p l07
%cd l07
!curl -L -C -  https://fb.me/multilingual_task_oriented_data  -o data.zip
%cd ..

C:\Users\Ania\Desktop\System_Dialogowy_Janet\l07
C:\Users\Ania\Desktop\System_Dialogowy_Janet


  % Total    % Received % Xferd  Average Speed   Time    Time     Time  Current
                                 Dload  Upload   Total   Spent    Left  Speed

  0     0    0     0    0     0      0      0 --:--:-- --:--:-- --:--:--     0
  0     0    0     0    0     0      0      0 --:--:-- --:--:-- --:--:--     0
  0     0    0     0    0     0      0      0 --:--:-- --:--:-- --:--:--     0

  0 8714k    0  1656    0     0    886      0  2:47:51  0:00:01  2:47:50   886
  4 8714k    4  406k    0     0   167k      0  0:00:52  0:00:02  0:00:50  721k
 33 8714k   33 2957k    0     0   863k      0  0:00:10  0:00:03  0:00:07 1898k
 69 8714k   69 6035k    0     0  1387k      0  0:00:06  0:00:04  0:00:02 2429k
100 8714k  100 8714k    0     0  1703k      0  0:00:05  0:00:05 --:--:-- 2683k


Zbiór ten gromadzi wypowiedzi w trzech językach opisane slotami dla dwunastu ram należących do trzech dziedzin `Alarm`, `Reminder` oraz `Weather`. Dane wczytamy korzystając z biblioteki [conllu](https://pypi.org/project/conllu/).

In [2]:
!pip3 install conllu
import codecs
from conllu import parse_incr
fields = ['id', 'form', 'frame', 'slot']

def nolabel2o(line, i):
    return 'O' if line[i] == 'NoLabel' else line[i]

with open('Janet.conllu', encoding='utf-8') as trainfile:
    trainset = list(parse_incr(trainfile, fields=fields, field_parsers={'slot': nolabel2o}))
with open('Janet.conllu', encoding='utf-8') as testfile:
    testset = list(parse_incr(testfile, fields=fields, field_parsers={'slot': nolabel2o}))

Zobaczmy kilka przykładowych wypowiedzi z tego zbioru.

In [3]:
!pip3 install tabulate
from tabulate import tabulate
tabulate(trainset[0], tablefmt='html')

'<table>\n<tbody>\n<tr><td style="text-align: right;">1</td><td>chciałem </td><td>appointment/request_prescription</td><td>O                  </td></tr>\n<tr><td style="text-align: right;">2</td><td>prosić   </td><td>appointment/request_prescription</td><td>O                  </td></tr>\n<tr><td style="text-align: right;">3</td><td>o        </td><td>appointment/request_prescription</td><td>O                  </td></tr>\n<tr><td style="text-align: right;">4</td><td>wypisanie</td><td>appointment/request_prescription</td><td>O                  </td></tr>\n<tr><td style="text-align: right;">5</td><td>kolejnej </td><td>appointment/request_prescription</td><td>O                  </td></tr>\n<tr><td style="text-align: right;">6</td><td>recepty  </td><td>appointment/request_prescription</td><td>B-prescription     </td></tr>\n<tr><td style="text-align: right;">7</td><td>na       </td><td>appointment/request_prescription</td><td>O                  </td></tr>\n<tr><td style="text-align: right;">8</td><td>lek      </td><td>appointment/request_prescription</td><td>B-prescription/type</td></tr>\n<tr><td style="text-align: right;">9</td><td>x        </td><td>appointment/request_prescription</td><td>I-prescription/type</td></tr>\n</tbody>\n</table>'

Na potrzeby prezentacji procesu uczenia w jupyterowym notatniku zawęzimy zbiór danych do początkowych przykładów.

Budując model skorzystamy z architektury opartej o rekurencyjne sieci neuronowe
zaimplementowanej w bibliotece [flair](https://github.com/flairNLP/flair) (Akbik i in. 2018).

In [4]:
!pip3 install flair

In [5]:
from flair.data import Corpus, Sentence, Token
from flair.datasets import SentenceDataset
from flair.embeddings import StackedEmbeddings
from flair.embeddings import WordEmbeddings
from flair.embeddings import CharacterEmbeddings
from flair.embeddings import FlairEmbeddings
from flair.models import SequenceTagger
from flair.trainers import ModelTrainer

!pip3 install torch
# determinizacja obliczeń
import random
import torch
random.seed(42)
torch.manual_seed(42)

if torch.cuda.is_available():
    torch.cuda.manual_seed(0)
    torch.cuda.manual_seed_all(0)
    torch.backends.cudnn.enabled = False
    torch.backends.cudnn.benchmark = False
    torch.backends.cudnn.deterministic = True

Dane skonwertujemy do formatu wykorzystywanego przez `flair`, korzystając z następującej funkcji.

In [6]:
def conllu2flair(sentences, label=None):
    fsentences = []

    for sentence in sentences:
        fsentence = Sentence()

        for token in sentence:
            ftoken = Token(token['form'])

            if label:
                ftoken.add_tag(label, token[label])

            fsentence.add_token(ftoken)

        fsentences.append(fsentence)

    return SentenceDataset(fsentences)

corpus = Corpus(train=conllu2flair(trainset, 'slot'), test=conllu2flair(testset, 'slot'))
print(corpus)
tag_dictionary = corpus.make_tag_dictionary(tag_type='slot')
print(tag_dictionary)

Corpus: 99 train + 11 dev + 110 test sentences
Dictionary with 31 tags: <unk>, O, B-prescription, B-prescription/type, I-prescription/type, B-end_conversation, B-deny, I-end_conversation, B-greeting, I-greeting, B-appointment, B-appointment/doctor, I-appointment/doctor, B-datetime, NoLabel I-end_conversation, I-datetime, B-affirm, B-appointment/office, I-B-datetime, B-results, B-appointment/type, I-appointment/type, B-register/email, B-doctor, I-affirm, B-appoinment/doctor, B-appoinment, B-register/name, I-register/name, <START>


Nasz model będzie wykorzystywał wektorowe reprezentacje słów (zob. [Word Embeddings](https://github.com/flairNLP/flair/blob/master/resources/docs/TUTORIAL_3_WORD_EMBEDDING.md)).

In [7]:
embedding_types = [
    WordEmbeddings('pl'),
    FlairEmbeddings('pl-forward'),
    FlairEmbeddings('pl-backward'),
    CharacterEmbeddings(),
]

embeddings = StackedEmbeddings(embeddings=embedding_types)
tagger = SequenceTagger(hidden_size=256, embeddings=embeddings,
                        tag_dictionary=tag_dictionary,
                        tag_type='slot', use_crf=True)

Zobaczmy jak wygląda architektura sieci neuronowej, która będzie odpowiedzialna za przewidywanie
slotów w wypowiedziach.

In [8]:
print(tagger)

SequenceTagger(
  (embeddings): StackedEmbeddings(
    (list_embedding_0): WordEmbeddings('pl')
    (list_embedding_1): FlairEmbeddings(
      (lm): LanguageModel(
        (drop): Dropout(p=0.25, inplace=False)
        (encoder): Embedding(1602, 100)
        (rnn): LSTM(100, 2048)
        (decoder): Linear(in_features=2048, out_features=1602, bias=True)
      )
    )
    (list_embedding_2): FlairEmbeddings(
      (lm): LanguageModel(
        (drop): Dropout(p=0.25, inplace=False)
        (encoder): Embedding(1602, 100)
        (rnn): LSTM(100, 2048)
        (decoder): Linear(in_features=2048, out_features=1602, bias=True)
      )
    )
    (list_embedding_3): CharacterEmbeddings(
      (char_embedding): Embedding(275, 25)
      (char_rnn): LSTM(25, 25, bidirectional=True)
    )
  )
  (word_dropout): WordDropout(p=0.05)
  (locked_dropout): LockedDropout(p=0.5)
  (embedding2nn): Linear(in_features=4446, out_features=4446, bias=True)
  (rnn): LSTM(4446, 256, batch_first=True, bidirectiona

Wykonamy dziesięć iteracji (epok) uczenia a wynikowy model zapiszemy w katalogu `slot-model`.

In [9]:
trainer = ModelTrainer(tagger, corpus)
trainer.train('slot-model',
              learning_rate=0.1,
              mini_batch_size=32,
              max_epochs=100,
              train_with_dev=False)

2021-05-16 19:11:09,838 ----------------------------------------------------------------------------------------------------
2021-05-16 19:11:09,846 Model: "SequenceTagger(
  (embeddings): StackedEmbeddings(
    (list_embedding_0): WordEmbeddings('pl')
    (list_embedding_1): FlairEmbeddings(
      (lm): LanguageModel(
        (drop): Dropout(p=0.25, inplace=False)
        (encoder): Embedding(1602, 100)
        (rnn): LSTM(100, 2048)
        (decoder): Linear(in_features=2048, out_features=1602, bias=True)
      )
    )
    (list_embedding_2): FlairEmbeddings(
      (lm): LanguageModel(
        (drop): Dropout(p=0.25, inplace=False)
        (encoder): Embedding(1602, 100)
        (rnn): LSTM(100, 2048)
        (decoder): Linear(in_features=2048, out_features=1602, bias=True)
      )
    )
    (list_embedding_3): CharacterEmbeddings(
      (char_embedding): Embedding(275, 25)
      (char_rnn): LSTM(25, 25, bidirectional=True)
    )
  )
  (word_dropout): WordDropout(p=0.05)
  (locked_dr

2021-05-16 19:12:14,648 EPOCH 7 done: loss 7.0163 - lr 0.1000000
2021-05-16 19:12:14,745 DEV : loss 5.496520519256592 - score 0.1538
2021-05-16 19:12:14,745 BAD EPOCHS (no improvement): 0
saving best model
2021-05-16 19:12:24,553 ----------------------------------------------------------------------------------------------------
2021-05-16 19:12:25,305 epoch 8 - iter 1/4 - loss 5.84166050 - samples/sec: 43.01 - lr: 0.100000
2021-05-16 19:12:26,009 epoch 8 - iter 2/4 - loss 5.58190751 - samples/sec: 45.43 - lr: 0.100000
2021-05-16 19:12:26,803 epoch 8 - iter 3/4 - loss 6.09121291 - samples/sec: 40.28 - lr: 0.100000
2021-05-16 19:12:27,011 epoch 8 - iter 4/4 - loss 5.20219183 - samples/sec: 153.85 - lr: 0.100000
2021-05-16 19:12:27,011 ----------------------------------------------------------------------------------------------------
2021-05-16 19:12:27,011 EPOCH 8 done: loss 5.2022 - lr 0.1000000
2021-05-16 19:12:27,099 DEV : loss 5.2129292488098145 - score 0.3478
2021-05-16 19:12:27,0

2021-05-16 19:13:26,483 ----------------------------------------------------------------------------------------------------
2021-05-16 19:13:26,483 EPOCH 17 done: loss 4.0345 - lr 0.1000000
2021-05-16 19:13:26,579 DEV : loss 3.864961862564087 - score 0.6154
2021-05-16 19:13:26,580 BAD EPOCHS (no improvement): 2
2021-05-16 19:13:26,583 ----------------------------------------------------------------------------------------------------
2021-05-16 19:13:27,322 epoch 18 - iter 1/4 - loss 3.06332946 - samples/sec: 43.30 - lr: 0.100000
2021-05-16 19:13:27,901 epoch 18 - iter 2/4 - loss 3.11640310 - samples/sec: 55.27 - lr: 0.100000
2021-05-16 19:13:28,698 epoch 18 - iter 3/4 - loss 2.99107130 - samples/sec: 40.18 - lr: 0.100000
2021-05-16 19:13:28,898 epoch 18 - iter 4/4 - loss 2.94846284 - samples/sec: 160.00 - lr: 0.100000
2021-05-16 19:13:28,898 ----------------------------------------------------------------------------------------------------
2021-05-16 19:13:28,898 EPOCH 18 done: loss

2021-05-16 19:13:51,642 epoch 27 - iter 3/4 - loss 1.91284267 - samples/sec: 43.46 - lr: 0.025000
2021-05-16 19:13:51,834 epoch 27 - iter 4/4 - loss 2.51718122 - samples/sec: 166.65 - lr: 0.025000
2021-05-16 19:13:51,834 ----------------------------------------------------------------------------------------------------
2021-05-16 19:13:51,834 EPOCH 27 done: loss 2.5172 - lr 0.0250000
2021-05-16 19:13:51,930 DEV : loss 3.624786376953125 - score 0.6667
Epoch    27: reducing learning rate of group 0 to 1.2500e-02.
2021-05-16 19:13:51,930 BAD EPOCHS (no improvement): 4
2021-05-16 19:13:51,930 ----------------------------------------------------------------------------------------------------
2021-05-16 19:13:52,650 epoch 28 - iter 1/4 - loss 2.06657982 - samples/sec: 44.45 - lr: 0.012500
2021-05-16 19:13:53,405 epoch 28 - iter 2/4 - loss 2.16739893 - samples/sec: 42.42 - lr: 0.012500
2021-05-16 19:13:54,234 epoch 28 - iter 3/4 - loss 1.87206562 - samples/sec: 38.60 - lr: 0.012500
2021-05-

2021-05-16 19:14:17,771 epoch 37 - iter 1/4 - loss 1.59361398 - samples/sec: 42.71 - lr: 0.003125
2021-05-16 19:14:18,573 epoch 37 - iter 2/4 - loss 1.86242718 - samples/sec: 39.93 - lr: 0.003125
2021-05-16 19:14:19,367 epoch 37 - iter 3/4 - loss 1.84938045 - samples/sec: 40.27 - lr: 0.003125
2021-05-16 19:14:19,575 epoch 37 - iter 4/4 - loss 1.94639012 - samples/sec: 159.98 - lr: 0.003125
2021-05-16 19:14:19,575 ----------------------------------------------------------------------------------------------------
2021-05-16 19:14:19,575 EPOCH 37 done: loss 1.9464 - lr 0.0031250
2021-05-16 19:14:19,663 DEV : loss 3.4721953868865967 - score 0.6667
2021-05-16 19:14:19,663 BAD EPOCHS (no improvement): 2
2021-05-16 19:14:19,663 ----------------------------------------------------------------------------------------------------
2021-05-16 19:14:20,420 epoch 38 - iter 1/4 - loss 1.87127459 - samples/sec: 42.26 - lr: 0.003125
2021-05-16 19:14:21,214 epoch 38 - iter 2/4 - loss 1.65014571 - sampl

2021-05-16 19:14:44,516 DEV : loss 3.467272996902466 - score 0.6667
2021-05-16 19:14:44,516 BAD EPOCHS (no improvement): 3
2021-05-16 19:14:44,516 ----------------------------------------------------------------------------------------------------
2021-05-16 19:14:45,083 epoch 47 - iter 1/4 - loss 1.17524457 - samples/sec: 57.22 - lr: 0.000781
2021-05-16 19:14:45,804 epoch 47 - iter 2/4 - loss 1.69363821 - samples/sec: 44.40 - lr: 0.000781
2021-05-16 19:14:46,515 epoch 47 - iter 3/4 - loss 1.80291025 - samples/sec: 45.00 - lr: 0.000781
2021-05-16 19:14:46,744 epoch 47 - iter 4/4 - loss 1.68751404 - samples/sec: 139.56 - lr: 0.000781
2021-05-16 19:14:46,744 ----------------------------------------------------------------------------------------------------
2021-05-16 19:14:46,744 EPOCH 47 done: loss 1.6875 - lr 0.0007813
2021-05-16 19:14:46,841 DEV : loss 3.4656827449798584 - score 0.6667
Epoch    47: reducing learning rate of group 0 to 3.9063e-04.
2021-05-16 19:14:46,841 BAD EPOCHS (n

2021-05-16 19:15:14,421 ----------------------------------------------------------------------------------------------------
2021-05-16 19:15:14,421 Testing using best model ...
2021-05-16 19:15:14,426 loading file slot-model\best-model.pt
2021-05-16 19:15:34,103 0.6759	0.6901	0.6829
2021-05-16 19:15:34,103 
Results:
- F1-score (micro) 0.6829
- F1-score (macro) 0.3185

By class:
NoLabel I-end_conversation tp: 0 - fp: 0 - fn: 2 - precision: 0.0000 - recall: 0.0000 - f1-score: 0.0000
affirm     tp: 11 - fp: 6 - fn: 2 - precision: 0.6471 - recall: 0.8462 - f1-score: 0.7333
appoinment tp: 0 - fp: 0 - fn: 2 - precision: 0.0000 - recall: 0.0000 - f1-score: 0.0000
appoinment/doctor tp: 0 - fp: 0 - fn: 2 - precision: 0.0000 - recall: 0.0000 - f1-score: 0.0000
appointment tp: 19 - fp: 4 - fn: 1 - precision: 0.8261 - recall: 0.9500 - f1-score: 0.8837
appointment/doctor tp: 16 - fp: 13 - fn: 5 - precision: 0.5517 - recall: 0.7619 - f1-score: 0.6400
appointment/office tp: 0 - fp: 0 - fn: 1 - preci

{'test_score': 0.6829268292682927,
 'dev_score_history': [0.0,
  0.0,
  0.0,
  0.0,
  0.06451612903225808,
  0.0,
  0.15384615384615383,
  0.34782608695652173,
  0.2608695652173913,
  0.30769230769230765,
  0.34782608695652173,
  0.3333333333333333,
  0.4615384615384615,
  0.43478260869565216,
  0.6923076923076924,
  0.5833333333333334,
  0.6153846153846153,
  0.48000000000000004,
  0.5185185185185186,
  0.5599999999999999,
  0.5599999999999999,
  0.6666666666666666,
  0.5833333333333334,
  0.5833333333333334,
  0.6666666666666666,
  0.6666666666666666,
  0.6666666666666666,
  0.6666666666666666,
  0.6666666666666666,
  0.6666666666666666,
  0.5833333333333334,
  0.5833333333333334,
  0.6666666666666666,
  0.6666666666666666,
  0.6666666666666666,
  0.6666666666666666,
  0.6666666666666666,
  0.6666666666666666,
  0.6666666666666666,
  0.6666666666666666,
  0.6666666666666666,
  0.6666666666666666,
  0.6666666666666666,
  0.6666666666666666,
  0.6666666666666666,
  0.6666666666666666,


Jakość wyuczonego modelu możemy ocenić, korzystając z zaraportowanych powyżej metryk, tj.:

 - *tp (true positives)*

   > liczba słów oznaczonych w zbiorze testowym etykietą $e$, które model oznaczył tą etykietą

 - *fp (false positives)*

   > liczba słów nieoznaczonych w zbiorze testowym etykietą $e$, które model oznaczył tą etykietą

 - *fn (false negatives)*

   > liczba słów oznaczonych w zbiorze testowym etykietą $e$, którym model nie nadał etykiety $e$

 - *precision*

   > $$\frac{tp}{tp + fp}$$

 - *recall*

   > $$\frac{tp}{tp + fn}$$

 - $F_1$

   > $$\frac{2 \cdot precision \cdot recall}{precision + recall}$$

 - *micro* $F_1$

   > $F_1$ w którym $tp$, $fp$ i $fn$ są liczone łącznie dla wszystkich etykiet, tj. $tp = \sum_{e}{{tp}_e}$, $fn = \sum_{e}{{fn}_e}$, $fp = \sum_{e}{{fp}_e}$

 - *macro* $F_1$

   > średnia arytmetyczna z $F_1$ obliczonych dla poszczególnych etykiet z osobna.

Wyuczony model możemy wczytać z pliku korzystając z metody `load`.

In [10]:
model = SequenceTagger.load('slot-model/final-model.pt')

2021-05-16 19:15:34,133 loading file slot-model/final-model.pt


Wczytany model możemy wykorzystać do przewidywania slotów w wypowiedziach użytkownika, korzystając
z przedstawionej poniżej funkcji `predict`.

In [11]:
def predict(model, sentence):
    csentence = [{'form': word} for word in sentence]
    fsentence = conllu2flair([csentence])[0]
    model.predict(fsentence)
    return [(token, ftoken.get_tag('slot').value) for token, ftoken in zip(sentence, fsentence)]


Jak pokazuje przykład poniżej model wyuczony tylko na 100 przykładach popełnia w dosyć prostej
wypowiedzi błąd etykietując słowo `alarm` tagiem `B-weather/noun`.

In [15]:
tabulate(predict(model, ' dzien dobry poprosze wizytę do doktor lekarza rodzinnego najlepiej dzisiaj w godzinach popołudniowych dziś albo jutro internisty'.split()), tablefmt='html')

'<table>\n<tbody>\n<tr><td>dzien         </td><td>B-greeting          </td></tr>\n<tr><td>dobry         </td><td>I-greeting          </td></tr>\n<tr><td>poprosze      </td><td>O                   </td></tr>\n<tr><td>wizytę        </td><td>B-appointment       </td></tr>\n<tr><td>do            </td><td>O                   </td></tr>\n<tr><td>doktor        </td><td>B-appointment/doctor</td></tr>\n<tr><td>lekarza       </td><td>B-appointment/doctor</td></tr>\n<tr><td>rodzinnego    </td><td>I-appointment/doctor</td></tr>\n<tr><td>najlepiej     </td><td>O                   </td></tr>\n<tr><td>dzisiaj       </td><td>O                   </td></tr>\n<tr><td>w             </td><td>O                   </td></tr>\n<tr><td>godzinach     </td><td>I-datetime          </td></tr>\n<tr><td>popołudniowych</td><td>I-datetime          </td></tr>\n<tr><td>dziś          </td><td>B-datetime          </td></tr>\n<tr><td>albo          </td><td>O                   </td></tr>\n<tr><td>jutro         </td><td>I-datetime          </td></tr>\n<tr><td>internisty    </td><td>I-appointment/doctor</td></tr>\n</tbody>\n</table>'

Literatura
----------
 1. Sebastian Schuster, Sonal Gupta, Rushin Shah, Mike Lewis, Cross-lingual Transfer Learning for Multilingual Task Oriented Dialog. NAACL-HLT (1) 2019, pp. 3795-3805
 2. John D. Lafferty, Andrew McCallum, and Fernando C. N. Pereira. 2001. Conditional Random Fields: Probabilistic Models for Segmenting and Labeling Sequence Data. In Proceedings of the Eighteenth International Conference on Machine Learning (ICML '01). Morgan Kaufmann Publishers Inc., San Francisco, CA, USA, 282–289, https://repository.upenn.edu/cgi/viewcontent.cgi?article=1162&context=cis_papers
 3. Sepp Hochreiter and Jürgen Schmidhuber. 1997. Long Short-Term Memory. Neural Comput. 9, 8 (November 15, 1997), 1735–1780, https://doi.org/10.1162/neco.1997.9.8.1735
 4. Ashish Vaswani, Noam Shazeer, Niki Parmar, Jakob Uszkoreit, Llion Jones, Aidan N. Gomez, Lukasz Kaiser, Illia Polosukhin, Attention is All you Need, NIPS 2017, pp. 5998-6008, https://arxiv.org/abs/1706.03762
 5. Alan Akbik, Duncan Blythe, Roland Vollgraf, Contextual String Embeddings for Sequence Labeling, Proceedings of the 27th International Conference on Computational Linguistics, pp. 1638–1649, https://www.aclweb.org/anthology/C18-1139.pdf
